# HW # 6 
by Vira Shulha


In [1]:
import tarfile
import os
import nltk
import numpy as np
import numpy.matlib
import scipy
nltk.download('punkt')
nltk.adownload('averaged_perceptron_tagger') 
nltk.download('wordnet') 
nltk.download('stopwords')
nltk.download('omw-1.4')
lemmatizer = nltk.stem.WordNetLemmatizer() 

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Vera\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


AttributeError: module 'nltk' has no attribute 'adownload'

# 1 a)

In [2]:
newsgroups_file = tarfile.open('C:/disk_D/1_tampere_uni/text data analysis/hw/6/20news-19997.tar.gz')
newsgroups_file = newsgroups_file.extractall('C:/disk_D/1_tampere_uni/text data analysis/hw/6/')

KeyboardInterrupt: 

# 1 b)

In [2]:
topics = ['rec.autos', 'rec.motorcycles', 'rec.sport.baseball', 'rec.sport.hockey']
newsgroup_topics_documents = []
for topic in topics:
    path_to_topic = 'C:/disk_D/1_tampere_uni/text data analysis/hw/6/20_newsgroups/' + topic
    topic_documents_names = os.listdir(path_to_topic)[:500]
    topic_documents = []
    for topic_document_name in topic_documents_names:
        document_file = open(path_to_topic + '/' + topic_document_name, 'r')
        document = document_file.read()
        document_file.close()
        newsgroup_topics_documents.append(document)

In [3]:
excludedlinemarkers=['Xref:','Path:','From:','Newsgroups:','Subject:','Summary:', \
                     'Keywords:','Message-ID:','Date:','Expires:','Followup-To:','Distribution:', \
                     'Organization:','Approved:','Supersedes:','Lines:','NNTP-Posting-Host:', \
                     'References:','Sender:','In-Reply-To:','Article-I.D.:','Reply-To:', \
                     'Nntp-Posting-Host:'] 

for d_document in range(len(newsgroup_topics_documents)):
    templines = newsgroup_topics_documents[d_document].splitlines()    
    remaininglines = []    
    for l in range(len(templines)):        
        line_should_be_excluded = 0        
        for m in range(len(excludedlinemarkers)):            
            if len(templines[l]) >= len(excludedlinemarkers[m]):                
                if excludedlinemarkers[m] == \
                                templines[l][0:len(excludedlinemarkers[m])]:                    
                    line_should_be_excluded=1                    
                    break        
        if line_should_be_excluded == 0:           
            remaininglines.append(templines[l])    
    newsgroup_topics_documents[d_document] = '\n'.join(remaininglines)

In [4]:
def tokenize_text(text):
    
    temp_tokenizedtext = nltk.word_tokenize(text)    
    mycrawled_nltktext = nltk.Text(temp_tokenizedtext)    
    
    return mycrawled_nltktext


def lower_case_text(text):
    mycrawled_lowercasetext = [] 

    for k in range(len(text)):        
        lowercaseword = text[k].lower()        
        mycrawled_lowercasetext.append(lowercaseword)    
        
    return mycrawled_lowercasetext

def tagtowordnet(postag):   
    wordnettag = -1   
    if postag[0] == 'N':        
        wordnettag = 'n'   
    elif postag[0] == 'V':        
        wordnettag = 'v'   
    elif postag[0] == 'J':        
        wordnettag = 'a'    
    elif postag[0] == 'R':        
        wordnettag = 'r'    
    return(wordnettag)

def lemmatizetext(nltktexttolemmatize):    
    # Tag the text with POS tags    
    taggedtext = nltk.pos_tag(nltktexttolemmatize)   
    # Lemmatize each word text    
    lemmatizedtext = []    
    for l in range(len(taggedtext)):       
        # Lemmatize a word using the WordNet converted POS tag       
        wordtolemmatize = taggedtext[l][0]        
        wordnettag = tagtowordnet(taggedtext[l][1])        
        if wordnettag != -1:            
            lemmatizedword = lemmatizer.lemmatize(wordtolemmatize,wordnettag)        
        else:            
            lemmatizedword=wordtolemmatize       
            # Store the lemmatized word        
        lemmatizedtext.append(lemmatizedword)
        
    return(lemmatizedtext) 


In [6]:
def prune_text(mycrawled_lemmatizedtexts, unifiedvocabulary, myindices_in_unifiedvocabulary,  highest_totaloccurrences_indices, occur_counts):
    nltkstopwords=nltk.corpus.stopwords.words('english') 
    pruningdecisions = np.zeros((len(unifiedvocabulary),1)) 
    for k in range(len(unifiedvocabulary)):    
        # Rule 1: check the nltk stop word list    
        if (unifiedvocabulary[k] in nltkstopwords):        
            pruningdecisions[k] = 1    
            
        # Rule 2: if the word is in the top 1% of frequent words    
        if (k in highest_totaloccurrences_indices[\
                                                  0:int(np.floor(len(unifiedvocabulary)*0.01))]):        
            pruningdecisions[k] = 1    
        # Rule 3: if the word is too short    
        if len(unifiedvocabulary[k]) < 2:        
            pruningdecisions[k] = 1    
            
        # Rule 4: if the word is in the bottom 65% of frequent words    
        if (k in highest_totaloccurrences_indices[(int(np.floor(\
                                                                len(unifiedvocabulary)*0.35))):len(unifiedvocabulary)]):        
            pruningdecisions[k]=1     
            
        # Rule 5: if the word is too long    
        if len(unifiedvocabulary[k])>20:        
            pruningdecisions[k] = 1    
            
        # Rule 6: if the word appears less than 4 times
        if occur_counts[k] < 4:
            pruningdecisions[k] = 1  
            
        if unifiedvocabulary[k].isalpha() == False:        
            pruningdecisions[k]=1
         
    oldtopruned = [] 
    tempind = -1 
    for k in range(len(unifiedvocabulary)):    
        if pruningdecisions[k] == 0:        
            tempind = tempind + 1        
            oldtopruned.append(tempind)    
        else:        
            oldtopruned.append(-1) 
    #%% Create pruned texts 
    mycrawled_prunedtexts = [] 
    myindices_in_prunedvocabulary = [] 
    for k in range(len(mycrawled_lemmatizedtexts)):       
        temp_newindices = []    
        temp_newdoc = []    
        for l in range(len(mycrawled_lemmatizedtexts[k])):        
            temp_oldindex = myindices_in_unifiedvocabulary[k][l]                    
            temp_newindex = oldtopruned[temp_oldindex]        
            if temp_newindex != -1:            
                temp_newindices.append(temp_newindex)            
                temp_newdoc.append(unifiedvocabulary[temp_oldindex])    
        mycrawled_prunedtexts.append(temp_newdoc)    
        myindices_in_prunedvocabulary.append(temp_newindices)
    
    remainingindices = np.squeeze(np.where(pruningdecisions == 0)[0]) 
    remainingvocabulary = unifiedvocabulary[remainingindices] 
    return mycrawled_prunedtexts, myindices_in_prunedvocabulary, remainingvocabulary

In [5]:
newsgroup_texts = []
for document in newsgroup_topics_documents:
    text = " ".join(document.split())
    newsgroup_texts.append(text)
    
newsgroups_tokenized = []
for document in newsgroup_texts:
    document = tokenize_text(document)
    newsgroups_tokenized.append(document)
    

newsgroups_lower = []
for document in newsgroups_tokenized:
    document = lower_case_text(document)
    newsgroups_lower.append(document)
    

newsgroups_texts_lemmatized = []
for document in newsgroups_lower:
    document = lemmatizetext(document)
    document = nltk.Text(document)
    newsgroups_texts_lemmatized.append(document)

NameError: name 'lemmatizer' is not defined

In [12]:
newsgroups_lower

[['in',
  'article',
  '<',
  'c4vir5.l3r',
  '@',
  'shuksan.ds.boeing.com',
  '>',
  ',',
  'fredd',
  '@',
  'shuksan',
  '(',
  'fred',
  'dickey',
  ')',
  'writes',
  ':',
  '|',
  '>',
  'carolinafan',
  '@',
  'uiuc',
  '(',
  'cka52397',
  '@',
  'uxa.cso.uiuc.edu',
  ')',
  'wrote',
  ':',
  '|',
  '>',
  ':',
  'i',
  'have',
  'been',
  'active',
  'in',
  'defending',
  'saturn',
  'lately',
  'on',
  'the',
  'net',
  'and',
  'would',
  '|',
  '>',
  ':',
  'like',
  'to',
  'state',
  'my',
  'full',
  'opinion',
  'on',
  'the',
  'subject',
  ',',
  'rather',
  'than',
  'just',
  'reply',
  'to',
  'others',
  "'",
  '|',
  '>',
  ':',
  'points',
  '.',
  '|',
  '>',
  ':',
  '|',
  '>',
  ':',
  'the',
  'biggest',
  'problem',
  'some',
  'people',
  'seem',
  'to',
  'be',
  'having',
  'is',
  'that',
  'saturn',
  '|',
  '>',
  ':',
  'dealers',
  'make',
  '~',
  '$',
  '2k',
  'on',
  'a',
  'car',
  '.',
  'i',
  'think',
  'most',
  'will',
  'agree',
  'wi

In [9]:
vocabularies = [] 
indices_in_vocabularies = []
# Find the vocabulary of each document 
for document in newsgroups_texts_lemmatized:   
    # Get unique words and where they occur       
    uniqueresults = np.unique(document,return_inverse=True)    
    uniquewords = uniqueresults[0]    
    wordindices = uniqueresults[1]    
    # Store the vocabulary and indices of document words in it    
    vocabularies.append(uniquewords)    
    indices_in_vocabularies.append(wordindices) 
    
tempvocabulary = []  
for document in newsgroups_texts_lemmatized:   
    tempvocabulary.extend(document) 
    # Find the unique elements among all vocabularies 
uniqueresults = np.unique(tempvocabulary,return_inverse=True) 
unifiedvocabulary = uniqueresults[0] 
wordindices = uniqueresults[1] 
# Translate previous indices to the unified vocabulary. 
# Must keep track where each vocabulary started in 
# the concatenated one. 
vocabularystart = 0 
indices_in_unifiedvocabulary = [] 
for k in range(len(newsgroups_texts_lemmatized)):    
    # In order to shift word indices, we must temporarily    
    # change their data type to a Numpy array    
    tempindices = np.array(indices_in_vocabularies[k])    
    tempindices = tempindices + vocabularystart    
    tempindices = wordindices[tempindices]    
    indices_in_unifiedvocabulary.append(tempindices)    
    vocabularystart = vocabularystart + len(vocabularies[k])
print(unifiedvocabulary)
'''   
unifiedvocabulary_totaloccurrencecounts = np.zeros((len(unifiedvocabulary),1)) 

for k in range(len(newsgroups_texts_lemmatized)): 
    occurrencecounts = np.zeros((len(unifiedvocabulary),1))    
    for l in range(len(indices_in_unifiedvocabulary[k])):        
        occurrencecounts[indices_in_unifiedvocabulary[k][l]] = \
        occurrencecounts[indices_in_unifiedvocabulary[k][l]] + 1    
    unifiedvocabulary_totaloccurrencecounts = \
    unifiedvocabulary_totaloccurrencecounts + occurrencecounts  

highest_totaloccurrences_indices = np.argsort(\
                                               -1*unifiedvocabulary_totaloccurrencecounts,axis=0) 

newsgroups_pruned_texts, vocabulary_pruned_indices, vocabulary_pruned = prune_text(newsgroups_texts_lemmatized, unifiedvocabulary, 
                                                                                  indices_in_unifiedvocabulary, 
                                                                                  unifiedvocabulary_totaloccurrencecounts,
                                                                                  highest_totaloccurrences_indices)
'''                                                                                 

[]


'   \nunifiedvocabulary_totaloccurrencecounts = np.zeros((len(unifiedvocabulary),1)) \n\nfor k in range(len(newsgroups_texts_lemmatized)): \n    occurrencecounts = np.zeros((len(unifiedvocabulary),1))    \n    for l in range(len(indices_in_unifiedvocabulary[k])):        \n        occurrencecounts[indices_in_unifiedvocabulary[k][l]] =         occurrencecounts[indices_in_unifiedvocabulary[k][l]] + 1    \n    unifiedvocabulary_totaloccurrencecounts =     unifiedvocabulary_totaloccurrencecounts + occurrencecounts  \n\nhighest_totaloccurrences_indices = np.argsort(                                               -1*unifiedvocabulary_totaloccurrencecounts,axis=0) \n\nnewsgroups_pruned_texts, vocabulary_pruned_indices, vocabulary_pruned = prune_text(newsgroups_texts_lemmatized, unifiedvocabulary, \n                                                                                  indices_in_unifiedvocabulary, \n                                                                                  uni

In [11]:
newsgroups_texts_lemmatized

[<Text: in article < c4vir5.l3r @ shuksan.ds.boeing.com > ,...>,
 <Text: in article < 1993apr5.135153.11132 @ wdl.loral.com > gwm...>,
 <Text: thanks to all of you who respond to...>,
 <Text: the subject say it all . my 1984...>,
 <Text: wolfson @ regatta.sps.mot.com ( stephen wolfson ) write...>,
 <Text: : tin [ version 1.1 pl8.8>,
 <Text: i 'm look for a replacement radio/tape player...>,
 <Text: i be think about get an infiniti g20...>,
 <Text: in article < 1993apr5.175719.7892 @ telxon.mis.telxon.com > joes...>,
 <Text: in article < 1993apr5.212645.15988 @ nntpd.lkg.dec.com > kenyon...>,
 <Text: in article < 3mwf2b1w165w @ njcc.wisdom.bubble.org > ,...>,
 <Text: do n't have a list of what 's...>,
 <Text: in article < 1993apr3.005245.10615 @ michael.apple.com > ems...>,
 <Text: in article < 1pq29p $ 29p @ seven-up.east.sun.com...>,
 <Text: news-software : vax/vms vnews 1.41 in article <...>,
 <Text: this past winter i drive from nyc to...>,
 <Text: sayeth `` joseph d. mazza '' < maz

# 1 c)

In [9]:
n_docs = len(newsgroups_pruned_texts) 
n_vocab = len(vocabulary_pruned) 
# Matrix of term frequencies 
tfmatrix_len_norm = scipy.sparse.lil_matrix((n_docs,n_vocab))
# Row vector of document frequencies 
dfvector = scipy.sparse.lil_matrix((1,n_vocab)) 
# Loop over documents 
for k in range(n_docs):   
    # Row vector of which words occurred in this document  
    temp_dfvector = scipy.sparse.lil_matrix((1,n_vocab))   
    temp_total_terms = len(np.unique(newsgroups_pruned_texts[k]))
    # Loop over words    
    for l in range(len(newsgroups_pruned_texts[k])):        
    # Add current word to term-frequency count and document-count        
        currentword = vocabulary_pruned_indices[k][l]   
        tfmatrix_len_norm[k,currentword] += 1  
        temp_dfvector[0,currentword] = 1  
    # Length normalization frequence of raw counts
    tfmatrix_len_norm[k, :] /= temp_total_terms
    # Add which words occurred in this document to overall document counts
    dfvector += temp_dfvector
    # Use the count statistics to compute the tf-idf matrix 
# Let's use length-normalized frequency term count, and smoothed logarithmic idf 


In [10]:
idfvector = 1 + np.log((1 / (np.array(dfvector.todense())[0] + 1)) * n_docs)
tfidfmatrix = scipy.sparse.lil_matrix((n_docs,n_vocab)) 
for k in range(n_docs):    
    tfidfmatrix[k,:] = tfmatrix_len_norm[k,:] * idfvector


# 1 d)

In [11]:
dimensiontotals = np.squeeze( \
                              np.array(np.sum(tfidfmatrix,axis=0))) 
highesttotals = np.argsort(-1*dimensiontotals) 
Xsmall = tfidfmatrix[:, highesttotals]

In [12]:
n_low_dimensions=10 
Uleft_10,D_10,UrightT_10 = scipy.sparse.linalg.svds(\
                                         Xsmall.todense(),k=n_low_dimensions)

# 1 e)

In [13]:
for factor in range(n_low_dimensions):
    topweights_indices = np.argsort(-1*np.abs(UrightT_10[factor,:]))
    print(vocabulary_pruned[highesttotals[topweights_indices[:10]]])

['viking' 'warrior' 'wcs' 'plus' 'connecticut' 'greenberg' 'gadgets'
 'mikey' 'criminal' 'guilty']
['inception' 'emblazon' 'stamber' 'pinstripe' 'historical' 'pugnaciously'
 'shunt' 'hilarious' 'evade' 'elitserien']
['honorable' 'surhoff' 'volkswagens' 'parenthesis' 'jukka' 'kuopio'
 'breath' 'register' 'vacation' 'clark']
['lately' 'educational' 'drozinst' 'hitter' 'development' 'occasional'
 'electron' 'kevinh' 'sweeter' 'bout']
['condiment' 'perfect' 'psychology' 'weary' 'testarossa' 'stern' 'egreen'
 'campus' 'precipitate' 'bowling']
['pg' 'dat' 'vince' 'age' 'oa' 'cry' 'space' 'evr' 'blah' 'patriots']
['boyo' 'simmon' 'lammers' 'cylinder' 'disco' 'furnishing' 'aquisition'
 'breaker' 'pancreas' 'hounslow']
['davew' 'swedish' 'ty' 'mitchell' 'carolina' 'throtle' 'activate'
 'atttributed' 'franciscoidle' 'hosed']
['markk' 'vous' 'pamuelle' 'grass' 'bleacher' 'camaros' 'tomorrow' 'deter'
 'pecota' 'cowl']
['aa' 'abotu' 'abott' 'abortion' 'aaa' 'aamir' 'aardvark' 'aargh' 'aaron'
 'ab']

Only a few factors seem to them related to the individual group. There is close to nothing common between real topics (autos, baseball, hockey, motorcycles. Most of them look meaningless. For example, the first factor has some common idea about battle or fight but not all words are connected to this topic.

# 1 f)

In [14]:
n_low_dimensions = 15
Uleft_15,D_15,UrightT_15 = scipy.sparse.linalg.svds(\
                                         Xsmall.todense(),k=n_low_dimensions)

In [15]:
for factor in range(n_low_dimensions):
    topweights_indices = np.argsort(-1*np.abs(UrightT_15[factor,:]))
    print(vocabulary_pruned[highesttotals[topweights_indices[:10]]])

['community' 'regular' 'indicate' 'yastrzemski' 'pasadena' 'weaver'
 'reasonably' 'publicity' 'skyline' 'jao']
['flames' 'order' 'watmath' 'flawless' 'opposite' 'cobra' 'yogi' 'casburn'
 'preserve' 'clusterf']
['waving' 'olaf' 'pundit' 'hasit' 'dancer' 'complimentary' 'thread'
 'allowance' 'yore' 'odjick']
['frenchies' 'dictate' 'sincere' 'branch' 'apprecisted' 'agressive'
 'bolton' 'standpoint' 'good' 'postpone']
['twetzel' 'carseat' 'readout' 'soup' 'advice' 'spica' 'klopfenstein'
 'cubbie' 'contradictory' 'dissappointed']
['conservatively' 'captain' 'encapsulate' 'attire' 'daemon' 'claim'
 'hardpressed' 'thx' 'ridiculously' 'straighten']
['nf' 'dagibbs' 'drake' 'mxmsd' 'cchb' 'ciccarelli' 'tuscon'
 'reproduction' 'organ' 'gift']
['gravitationally' 'absolute' 'roast' 'youm' 'unintentionally' 'july'
 'representative' 'wuz' 'nicmad' 'ewm']
['bushing' 'outlaw' 'lak' 'olympics' 'disappoint' 'ship' 'oba' 'pilon'
 'similarity' 'linkage']
['temper' 'burks' 'everybody' 'conine' 'hefty' 'fair

In [16]:
n_low_dimensions = 5
Uleft_5,D_5,UrightT_5 = scipy.sparse.linalg.svds(\
                                         Xsmall.todense(),k=n_low_dimensions)

In [17]:
for factor in range(n_low_dimensions):
    topweights_indices = np.argsort(-1*np.abs(UrightT_5[factor,:]))
    print(vocabulary_pruned[highesttotals[topweights_indices[:10]]])

['hk' 'ring' 'cryptography' 'da' 'merrier' 'ww' 'blazer' 'reinforce'
 'ryder' 'shion']
['adversary' 'karnak' 'gadget' 'lavishing' 'witty' 'liscence' 'correction'
 'barehanded' 'surgery' 'louisiana']
['espcially' 'outweigh' 'undercoat' 'lightly' 'style' 'pithy' 'yuk'
 'commonwealth' 'flied' 'lousy']
['opuglies' 'audi' 'viability' 'bldg' 'unreliable' 'resist' 'trucker'
 'ergonomic' 'richter' 'horner']
['aa' 'abotu' 'abott' 'abortion' 'aaa' 'aamir' 'aardvark' 'aargh' 'aaron'
 'ab']


Found 5 factors don't seem to make more sense. In my opinion, result with 10 factors is the best in my case (or something wrong with svd function here).

# 2 a)

In [20]:
n_docs = len(newsgroups_pruned_texts) 
n_vocab = len(vocabulary_pruned) 
# Matrix of term frequencies 
tfmatrix = scipy.sparse.lil_matrix((n_docs,n_vocab)) 
# Loop over documents 
for k in range(n_docs):   
    # Row vector of which words occurred in this document  
    temp_dfvector = scipy.sparse.lil_matrix((1,n_vocab))   
    temp_total_terms = len(np.unique(newsgroups_pruned_texts[k]))
    # Loop over words    
    for l in range(len(newsgroups_pruned_texts[k])):        
    # Add current word to term-frequency count and document-count        
        currentword = vocabulary_pruned_indices[k][l]   
        tfmatrix[k,currentword] += 1  

In [21]:
def plsa(document_to_word_matrix, n_topics, n_iterations):        
    n_docs = np.shape(document_to_word_matrix)[0]            
    # Number of documents and vocabulary words    
    n_vocab = np.shape(document_to_word_matrix)[1]           
    theta = scipy.stats.uniform.rvs(size=(n_vocab,n_topics))  
    # Prob of words per topic: random init    
    theta = theta/numpy.matlib.repmat(np.sum(theta,axis=0),n_vocab,1)        
    psi = scipy.stats.uniform.rvs(size=(n_topics,n_docs))     
    # Probs topics per document: random init    
    psi = psi/numpy.matlib.repmat(np.sum(psi,axis=0),n_topics,1)        
    n_words_in_docs = np.squeeze(np.array(\
                                                # Numbers of words in documents: computed once        
                                                np.sum(document_to_word_matrix,axis=1)))        
    n_totalwords = np.sum(n_words_in_docs)                 
    # Total number of words: computed once        
    pi = n_words_in_docs/n_totalwords                         
    # Document probs: computed once            
    for myiter in range(n_iterations):
        #print(myiter)
        # Perform Expectation-Maximization iterations        
        # ===Perform E-step====        
        doc_word_to_topics = []               
        # Compute theta_{v|t}psi_{t|d}/sum_t' theta_{v|t'}psi_{t'|d}         
        doc_word_to_topic_sum = np.zeros((n_docs,n_vocab))  
        for t in range(n_topics):            
            doc_word_to_topict = \
            numpy.matlib.repmat(theta[:,t],n_docs,1) * \
            numpy.matlib.repmat(psi[t,:],n_vocab,1).T                         
            myepsilon = 1e-8           
            # Add a positive number to avoid divisions by zero            
            doc_word_to_topict += myepsilon             
            doc_word_to_topics.append(doc_word_to_topict)            
            doc_word_to_topic_sum += doc_word_to_topict     
        #print('first loop done')
        for t in range(n_topics):            
            doc_word_to_topics[t] /= doc_word_to_topic_sum         
        # =======Perform M-step=======                                
        # Add a small number to word counts to avoid divisions by zero    
        #print('second done')
        for t in range(n_topics):                            
            # Compute document-to-topic probabilities.            
            psi[t,:] = np.squeeze(np.array(np.sum( \
                                                    np.multiply(document_to_word_matrix+myepsilon,doc_word_to_topics[t]),axis=1)))                
        psi /= numpy.matlib.repmat(np.sum(psi,axis=0),n_topics,1)     
        #print('third done')
        for t in range(n_topics):                            
            # Compute topic-to-word probabilities            
            theta[:,t] = np.squeeze(np.array(np.sum( \
                                                      np.multiply(document_to_word_matrix,doc_word_to_topics[t]),axis=0).T))               
        theta /= numpy.matlib.repmat(np.sum(theta,axis=0),n_vocab,1)   
        #print('last loop done')
    return(pi,psi,theta)

# 2 b)

In [22]:
dimensiontotals_plsa = np.squeeze( \
                              np.array(np.sum(tfmatrix,axis=0))) 
highesttotals_plsa = np.argsort(-1*dimensiontotals_plsa) 
Xsmall_plsa = tfmatrix[:, highesttotals_plsa]

# 2 c)

In [23]:
n_topics=10
n_iterations=100
pi,psi,theta=plsa(Xsmall_plsa.todense(), n_topics, n_iterations)

In [36]:
for factor in range(n_topics):
    print(factor)
    topweights_indices = np.argsort(-1*numpy.abs(theta[:,factor])) 
    print(vocabulary_pruned[highesttotals_plsa[topweights_indices[:10]]])

0
['car' 'safety' 'honda' 'may' 'show' 'identify' 'go' 'spafford' 'set'
 'use']
1
['problem' 'thread' 'drive' 'late' 'want' 'worry' 'oil' 'dal' 'never'
 'work']
2
['write' 'article' 'make' 'please' 'say' 'tread' 'rock' 'go' 'rider'
 'know']
3
['dod' 'write' 'article' 'list' 'marcl' 'stuff' 'give' 'pay' 'denver'
 'bike']
4
['would' 'bike' 'ride' 'afm' 'write' 'get' 'like' 'restore' 'opinion'
 'wear']
5
['side' 'look' 'move' 'retreat' 'hi' 'sure' 'much' 'idea' 'like' 'good']
6
['car' 'good' 'get' 'driver' 'engine' 'brake' 'flag' 'eric' 'job' 'one']
7
['available' 'time' 'unforeseen' 'motorcycle' 'write' 'article' 'get'
 'dog' 'bisquit' 'bright']
8
['first' 'one' 'nothing' 'well' 'twice' 'mark' 'take' 'throttle' 'bike'
 'write']
9
['car' 'team' 'one' 'really' 'system' 'article' 'mid' 'oh' 'write'
 'ventilation']


In the most of factors word "car" appears. This word appears a lot due to topic autos but here are other topics with the most common words. I see 4 factors which could be related to rec.autos. Factor 5 looks like a set of basic frequently used words. Also, the motorcycles topic stands out like the cars topic. Because I see at least 3 factors which have the word "bike" or "motorcycle".

# 2 d)

In [70]:
for factor in range(n_topics):
    print(factor)
    index_highest_proba_document = np.argsort(psi[factor,:])[-1]
    print(index_highest_proba_document)
    print(newsgroup_texts[index_highest_proba_document].split()[:100])
    print()

0
1263
["I'd", 'love', 'to', 'see', 'a', 'Shea', 'Stadium', 'gif.', '-Sean', '*******************************************************************************', '"Behind', 'the', 'bag!"', '-', 'Vin', 'Scully', '*******************************************************************************']

1
1005
['Giants', 'Win', 'the', 'Pennant!!', 'Giants', 'Win', 'the', 'Pennant', '!!', 'Gi...', 'OOOPS', 'I', 'guess', "I'm", 'a', 'little', 'early', 'here...', 'See', 'you', 'in', 'October...']

2
627
['>If', 'you', 'get', 'good', 'service', 'from', 'a', 'shop,', 'or', 'they', 'regularly', 'have', 'merchandise', '^^^^^^^', '>in', 'stock', 'you', 'need,', 'or', 'they', 'have', 'a', 'knowledgable', 'and/or', 'friendly', 'sales', '^^^^^^^^', '>staff,', 'or', 'if', 'for', 'whatever', 'other', 'reason', 'you', 'would', 'like', 'to', 'do', 'business', '>with', 'them,', 'which', 'will', 'in', 'the', 'aggrigate', 'keep', 'them', 'in', 'business', 'and', '>available', 'to', 'fill', 'your', 'future', 'needs,

# 3 g)

In [52]:
import gensim

gensim_dictionary = gensim.corpora.Dictionary(newsgroups_pruned_texts) 
gensim_docvectors = [] 
for k in range(len(newsgroups_pruned_texts)):         
    docvector = gensim_dictionary.doc2bow(newsgroups_pruned_texts[k])    
    gensim_docvectors.append(docvector)
    
numtopics = 10 
randomseed = 124574527 
numiters = 10000 
gensim_ldamodel = gensim.models.ldamodel.LdaModel( \
                                                gensim_docvectors, \
                                                id2word=gensim_dictionary, num_topics=numtopics, \
                                                iterations=numiters,random_state=randomseed)


In [53]:
gensim_termtopicprobabilities = gensim_ldamodel.get_topics() 
# Get topic prevalences per document, and overall topic prevalences 
# (expected amount of documents per topic) 
overallstrengths = np.zeros((numtopics,1)) 
documentstrengths = np.zeros((len(gensim_docvectors),numtopics)) 
for k in range(len(gensim_docvectors)):    
    topicstrengths = gensim_ldamodel.get_document_topics(\
                                                       gensim_docvectors[k],minimum_probability=0)   
    for m in range(len(topicstrengths)):        
        documentstrengths[k][topicstrengths[m][0]] = topicstrengths[m][1]       
        overallstrengths[topicstrengths[m][0]] = \
        overallstrengths[topicstrengths[m][0]] + topicstrengths[m][1]

# 3 h)

In [55]:
for factor in range(numtopics):
    print(factor)
    print(gensim_ldamodel.show_topic(factor,topn=10))
    print()

0
[('side', 0.030325323), ('team', 0.017124621), ('car', 0.012292279), ('look', 0.009159323), ('hi', 0.009121215), ('write', 0.009040043), ('article', 0.008736414), ('would', 0.007904972), ('go', 0.0074562887), ('new', 0.0065410347)]

1
[('spafford', 0.010729708), ('pay', 0.010411416), ('beth', 0.009689299), ('would', 0.008927978), ('car', 0.007744304), ('chuck', 0.0077108224), ('take', 0.006824008), ('please', 0.005537555), ('large', 0.0053761215), ('give', 0.005353382)]

2
[('would', 0.015297618), ('write', 0.01426447), ('ride', 0.010577073), ('dod', 0.010338033), ('worry', 0.00980418), ('get', 0.008986131), ('article', 0.007871584), ('denver', 0.0074132057), ('opinion', 0.007236463), ('car', 0.00630909)]

3
[('thread', 0.015979484), ('problem', 0.013329846), ('drive', 0.013224187), ('flag', 0.01256437), ('want', 0.010853524), ('try', 0.010084072), ('eric', 0.008679705), ('available', 0.008183411), ('later', 0.0071044737), ('motorcycle', 0.0068672756)]

4
[('late', 0.026407482), ('ma

A lot of words appear in the several factors. For example, the word "car" appears in 8 factors. From this, it can be assumed that more topics are selected than necessary. The close situation with words: ride, article, bike, get etc.

# 3 i)

In [60]:
for factor in range(numtopics):
    print(factor)
    index_highest_proba_document = np.argsort(documentstrengths[:,factor])[-1]
    print(index_highest_proba_document)
    print(newsgroup_texts[index_highest_proba_document].split()[:100])
    print()

0
1188
['Oops!', 'I', 'came', 'across', 'this', 'file', 'from', 'last', 'year.', 'Thought', 'you', 'might', 'enjoy', 'some', 'of', 'these', 'thoughts.', 'The', 'predictions', 'were', 'made', 'on', 'the', 'date', 'indicated.', 'They', 'are', 'largely', 'out', 'of', 'order.', '------------------------------------------------------------------------------', 'June', '11,', '1992', 'tedward@cs.cornell.edu', '(ME!)', '>What', 'have', 'I', 'done?', 'I', 'computed', 'the', '"expected', 'winning', 'percentage"', 'for', '>each', 'team', 'from', 'their', 'OBP,', 'total', 'bases,', 'and', 'runs', 'allowed.', 'I', 'use', 'the', '>basic', 'RC', 'formula', 'and', 'the', 'pythagorean', 'projection.', 'I', 'then', 'compare', 'this', '>with', 'their', 'actual', 'winning', 'percentage.', 'All', 'stats', 'through', 'June', '7.', '>', '>Team', 'OBP', 'TB', 'RA', 'W', 'L', 'XWP', 'Diff', '>baltimore', '0.351', '768', '199', '33', '21', '0.647', '-36', '>boston']

1
1386
['Here', 'is', 'the', 'OPI', '(Offens

I am surprised with the result because there are at least 3 texts about hockey topic but in the discovered most frequent words of factors, there isn't the word hockey. Also, I found at least 2 texts about the baseball match. It is more difficult to recognise texts about motorcycles and cars than I expected from the result of the most frequent words of topics.

# 3 k)

In [63]:
numtopics_1 = 15
gensim_ldamodel_1 = gensim.models.ldamodel.LdaModel( \
                                                gensim_docvectors, \
                                                id2word=gensim_dictionary, num_topics=numtopics_1, \
                                                iterations=numiters,random_state=randomseed)


In [65]:
gensim_termtopicprobabilities_1 = gensim_ldamodel_1.get_topics() 
# Get topic prevalences per document, and overall topic prevalences 
# (expected amount of documents per topic) 
overallstrengths_1 = np.zeros((numtopics_1,1)) 
documentstrengths_1 = np.zeros((len(gensim_docvectors),numtopics_1)) 
for k in range(len(gensim_docvectors)):    
    topicstrengths = gensim_ldamodel_1.get_document_topics(\
                                                       gensim_docvectors[k],minimum_probability=0)   
    for m in range(len(topicstrengths)):        
        documentstrengths_1[k][topicstrengths[m][0]] = topicstrengths[m][1]       
        overallstrengths_1[topicstrengths[m][0]] = \
        overallstrengths_1[topicstrengths[m][0]] + topicstrengths[m][1]

In [66]:
for factor in range(numtopics_1):
    print(factor)
    print(gensim_ldamodel_1.show_topic(factor,topn=10))
    print()

0
[('side', 0.033715375), ('team', 0.025917748), ('car', 0.015854554), ('write', 0.011274363), ('hi', 0.01028967), ('article', 0.009926806), ('would', 0.009326435), ('go', 0.007608707), ('predict', 0.0074313954), ('look', 0.0071455445)]

1
[('spafford', 0.017914644), ('would', 0.011217818), ('car', 0.009795031), ('pay', 0.008061456), ('speaks', 0.007940338), ('probably', 0.0077613248), ('please', 0.0075294576), ('may', 0.0070584295), ('large', 0.0069305957), ('air', 0.0060151718)]

2
[('would', 0.019634185), ('write', 0.01913354), ('worry', 0.015834147), ('dod', 0.014086017), ('opinion', 0.0111400345), ('get', 0.010475491), ('article', 0.0076316865), ('bike', 0.007540099), ('impact', 0.0066321944), ('go', 0.006020234)]

3
[('drive', 0.025803365), ('motorcycle', 0.013738925), ('try', 0.0122845145), ('article', 0.0090883095), ('load', 0.007979036), ('know', 0.007278643), ('apologize', 0.0070631094), ('write', 0.006935337), ('quite', 0.0064800084), ('jeq', 0.0052338466)]

4
[('marcl', 0.0

In [67]:
for factor in range(numtopics_1):
    print(factor)
    index_highest_proba_document = np.argsort(documentstrengths_1[:,factor])[-1]
    print(index_highest_proba_document)
    print(newsgroup_texts[index_highest_proba_document].split()[:100])
    print()

0
1188
['Oops!', 'I', 'came', 'across', 'this', 'file', 'from', 'last', 'year.', 'Thought', 'you', 'might', 'enjoy', 'some', 'of', 'these', 'thoughts.', 'The', 'predictions', 'were', 'made', 'on', 'the', 'date', 'indicated.', 'They', 'are', 'largely', 'out', 'of', 'order.', '------------------------------------------------------------------------------', 'June', '11,', '1992', 'tedward@cs.cornell.edu', '(ME!)', '>What', 'have', 'I', 'done?', 'I', 'computed', 'the', '"expected', 'winning', 'percentage"', 'for', '>each', 'team', 'from', 'their', 'OBP,', 'total', 'bases,', 'and', 'runs', 'allowed.', 'I', 'use', 'the', '>basic', 'RC', 'formula', 'and', 'the', 'pythagorean', 'projection.', 'I', 'then', 'compare', 'this', '>with', 'their', 'actual', 'winning', 'percentage.', 'All', 'stats', 'through', 'June', '7.', '>', '>Team', 'OBP', 'TB', 'RA', 'W', 'L', 'XWP', 'Diff', '>baltimore', '0.351', '768', '199', '33', '21', '0.647', '-36', '>boston']

1
663
['Southern', 'California', 'RideList',

I think the result of LDA with 15 factors has less sense than with 10. But the first 10 topics are the same as for LDA analysis with 10 factors. The last 5 topics are so close to the previous 10 in sense of appeared words. They look like a mix of previous topics.